In [12]:
import gymnasium as gym
from pogema import GridConfig
from stable_baselines3 import DQN, A2C
from stable_baselines3.common.evaluation import evaluate_policy

%load_ext autoreload
%autoreload 2
%matplotlib inline

grid_config = GridConfig(
    size=16,
    density=0.5,
    num_agents=1,
    max_episode_steps=64
)

env = gym.make("Pogema-v0",grid_config=grid_config)

a2c_model = A2C(
    "MlpPolicy",
    env,
    verbose=1
)

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload
Using cpu device
Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.


/Users/aditya/miniconda3/envs/pogema/lib/python3.9/site-packages/gymnasium/utils/passive_env_checker.py:29: UserWarning: WARN: It seems a Box observation space is an image but the `dtype` is not `np.uint8`, actual type: float32. If the Box observation space is not an image, we recommend flattening the observation to have only a 1D vector.
  logger.warn(
/Users/aditya/miniconda3/envs/pogema/lib/python3.9/site-packages/gymnasium/utils/passive_env_checker.py:34: UserWarning: WARN: It seems a Box observation space is an image but the lower and upper bounds are not [0, 255]. Actual lower bound: -1.0, upper bound: 1.0. Generally, CNN policies assume observations are within that range, so you may encounter an issue if the observation values are not.
  logger.warn(


#### Optuna Integration

In [13]:
""" Optuna example that optimizes the hyperparameters of
a reinforcement learning agent using A2C implementation from Stable-Baselines3
on a Gymnasium environment.

This is a simplified version of what can be found in https://github.com/DLR-RM/rl-baselines3-zoo.

You can run this example as follows:
    $ python sb3_simple.py

"""
from typing import Any
from typing import Dict

import gymnasium
import optuna
from optuna.pruners import MedianPruner
from optuna.samplers import TPESampler
from stable_baselines3 import A2C
from stable_baselines3.common.callbacks import EvalCallback
from stable_baselines3.common.monitor import Monitor
import torch
import torch.nn as nn


N_TRIALS = 100
N_STARTUP_TRIALS = 5
N_EVALUATIONS = 2
N_TIMESTEPS = int(5.0e5)
EVAL_FREQ = int(N_TIMESTEPS / N_EVALUATIONS)
N_EVAL_EPISODES = 3


DEFAULT_HYPERPARAMS = {
    "policy": "MlpPolicy",
    "verbose": 1,
    "env": env
}

def sample_a2c_params(trial: optuna.Trial) -> Dict[str, Any]:
    """Sampler for A2C hyperparameters."""
    gamma = 1.0 - trial.suggest_float("gamma", 0.0001, 0.1, log=True)
    learning_rate = trial.suggest_float("lr", 1e-5, 1, log=True)

    trial.set_user_attr("gamma", gamma)

    return {
        "gamma": gamma,
        "learning_rate": learning_rate,
    }


class TrialEvalCallback(EvalCallback):
    """Callback used for evaluating and reporting a trial."""

    def __init__(
        self,
        eval_env: gymnasium.Env,
        trial: optuna.Trial,
        n_eval_episodes: int = 5,
        eval_freq: int = 10000,
        deterministic: bool = True,
        verbose: int = 0,
    ):
        super().__init__(
            eval_env=eval_env,
            n_eval_episodes=n_eval_episodes,
            eval_freq=eval_freq,
            deterministic=deterministic,
            verbose=verbose,
        )
        self.trial = trial
        self.eval_idx = 0
        self.is_pruned = False

    def _on_step(self) -> bool:
        if self.eval_freq > 0 and self.n_calls % self.eval_freq == 0:
            super()._on_step()
            self.eval_idx += 1
            self.trial.report(self.last_mean_reward, self.eval_idx)
            # Prune trial if need.
            if self.trial.should_prune():
                self.is_pruned = True
                return False
        return True


def objective(trial: optuna.Trial) -> float:
    kwargs = DEFAULT_HYPERPARAMS.copy()
    # Sample hyperparameters.
    kwargs.update(sample_a2c_params(trial))
    # Create the RL model.
    model = A2C(**kwargs)
    # Create env used for evaluation.
    eval_env = Monitor(env)
    # Create the callback that will periodically evaluate and report the performance.
    eval_callback = TrialEvalCallback(
        eval_env, trial, n_eval_episodes=N_EVAL_EPISODES, eval_freq=EVAL_FREQ, deterministic=True
    )

    nan_encountered = False
    try:
        model.learn(N_TIMESTEPS, callback=eval_callback)
    except AssertionError as e:
        # Sometimes, random hyperparams can generate NaN.
        print(e)
        nan_encountered = True
    finally:
        # Free memory.
        model.env.close()
        eval_env.close()

    # Tell the optimizer that the trial failed.
    if nan_encountered:
        return float("nan")

    if eval_callback.is_pruned:
        raise optuna.exceptions.TrialPruned()

    return eval_callback.last_mean_reward


if __name__ == "__main__":
    # Set pytorch num threads to 1 for faster training.
    torch.set_num_threads(1)

    sampler = TPESampler(n_startup_trials=N_STARTUP_TRIALS)
    # Do not prune before 1/3 of the max budget is used.
    pruner = MedianPruner(n_startup_trials=N_STARTUP_TRIALS, n_warmup_steps=N_EVALUATIONS // 3)

    study = optuna.create_study(sampler=sampler, pruner=pruner, direction="maximize")
    try:
        study.optimize(objective, n_trials=N_TRIALS, n_jobs=4, timeout=600)
    except KeyboardInterrupt:
        pass

    print("Number of finished trials: ", len(study.trials))

    print("Best trial:")
    trial = study.best_trial

    print("  Value: ", trial.value)

    print("  Params: ")
    for key, value in trial.params.items():
        print("    {}: {}".format(key, value))

    print("  User attrs:")
    for key, value in trial.user_attrs.items():
        print("    {}: {}".format(key, value))


[I 2023-11-10 16:32:26,331] A new study created in memory with name: no-name-dd8452fc-2d9a-4acd-98a7-05526eb83ac5
[W ParallelNative.cpp:230] Warning: Cannot set number of intraop threads after parallel work has started or after set_num_threads call when using native parallel backend (function set_num_threads)


Using cpu device
Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.
Using cpu device
Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.
Using cpu device
Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.
Using cpu device
Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.
-------------------------------------
| rollout/              |           |
|    ep_len_mean        | 77        |
|    ep_rew_mean        | 0.333     |
| time/                 |           |
|    fps                | 233       |
|    iterations         | 100       |
|    time_elapsed       | 2         |
|    total_timesteps    | 500       |
| train/                |           |
|    entropy_loss       | -6.97e-08 |
|    explained_variance | 0.0151    |
|    learning_rate      | 0.056     |
|    n_updates          | 99        |
|    policy_loss        | -0        |
|    value_loss         | 0.012     |
----------------

[I 2023-11-10 17:19:43,726] Trial 2 finished with value: 1.0 and parameters: {'gamma': 0.03764379891594956, 'lr': 0.00010326521385250612}. Best is trial 2 with value: 1.0.


-------------------------------------
| rollout/              |           |
|    ep_len_mean        | 40.8      |
|    ep_rew_mean        | 0.5       |
| time/                 |           |
|    fps                | 167       |
|    iterations         | 95300     |
|    time_elapsed       | 2838      |
|    total_timesteps    | 476500    |
| train/                |           |
|    entropy_loss       | -7.38e-08 |
|    explained_variance | -0.703    |
|    learning_rate      | 0.056     |
|    n_updates          | 95299     |
|    policy_loss        | -0        |
|    value_loss         | 0.00384   |
-------------------------------------
------------------------------------
| rollout/              |          |
|    ep_len_mean        | 39.1     |
|    ep_rew_mean        | 0.54     |
| time/                 |          |
|    fps                | 166      |
|    iterations         | 94700    |
|    time_elapsed       | 2838     |
|    total_timesteps    | 473500   |
| train/             

[I 2023-11-10 17:21:11,297] Trial 3 finished with value: 0.0 and parameters: {'gamma': 0.01555985420195519, 'lr': 0.05595482406570459}. Best is trial 2 with value: 1.0.


------------------------------------
| rollout/              |          |
|    ep_len_mean        | 36.7     |
|    ep_rew_mean        | 0.48     |
| time/                 |          |
|    fps                | 169      |
|    iterations         | 99300    |
|    time_elapsed       | 2925     |
|    total_timesteps    | 496500   |
| train/                |          |
|    entropy_loss       | -1.22    |
|    explained_variance | -11.7    |
|    learning_rate      | 2.98e-05 |
|    n_updates          | 99299    |
|    policy_loss        | -0.0154  |
|    value_loss         | 0.000264 |
------------------------------------
------------------------------------
| rollout/              |          |
|    ep_len_mean        | 23.6     |
|    ep_rew_mean        | 0.73     |
| time/                 |          |
|    fps                | 164      |
|    iterations         | 96200    |
|    time_elapsed       | 2925     |
|    total_timesteps    | 481000   |
| train/                |          |
|

[I 2023-11-10 17:21:18,411] Trial 0 finished with value: 0.3333333333333333 and parameters: {'gamma': 0.017675360622156584, 'lr': 2.984311086096306e-05}. Best is trial 2 with value: 1.0.


-------------------------------------
| rollout/              |           |
|    ep_len_mean        | 20.7      |
|    ep_rew_mean        | 0.77      |
| time/                 |           |
|    fps                | 165       |
|    iterations         | 96900     |
|    time_elapsed       | 2932      |
|    total_timesteps    | 484500    |
| train/                |           |
|    entropy_loss       | -0.0424   |
|    explained_variance | 1.79e-07  |
|    learning_rate      | 0.00038   |
|    n_updates          | 96899     |
|    policy_loss        | -1.12e-05 |
|    value_loss         | 3.93e-06  |
-------------------------------------
-------------------------------------
| rollout/              |           |
|    ep_len_mean        | 22.9      |
|    ep_rew_mean        | 0.73      |
| time/                 |           |
|    fps                | 165       |
|    iterations         | 97000     |
|    time_elapsed       | 2932      |
|    total_timesteps    | 485000    |
| train/    

[I 2023-11-10 17:21:28,911] Trial 1 finished with value: 0.3333333333333333 and parameters: {'gamma': 0.00592817520938753, 'lr': 0.00038004764986176905}. Best is trial 2 with value: 1.0.


Number of finished trials:  4
Best trial:
  Value:  1.0
  Params: 
    gamma: 0.03764379891594956
    lr: 0.00010326521385250612
  User attrs:
    gamma: 0.9623562010840504


### Train agent with best hyper parameters

In [14]:
a2c_model = A2C(
    "MlpPolicy",
    env,
    verbose=1,
    gamma=1-0.03764379891594956,#0.005090895994889371,
    learning_rate=0.00010326521385250612#0.03807432884729837,
)

Using cpu device
Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.


In [15]:
# Train agent and save it
a2c_model.learn(int(5.0e5))
a2c_model.save("saved/a2c_b")

------------------------------------
| rollout/              |          |
|    ep_len_mean        | 38.4     |
|    ep_rew_mean        | 0.615    |
| time/                 |          |
|    fps                | 1397     |
|    iterations         | 100      |
|    time_elapsed       | 0        |
|    total_timesteps    | 500      |
| train/                |          |
|    entropy_loss       | -1.61    |
|    explained_variance | -8.9     |
|    learning_rate      | 0.000103 |
|    n_updates          | 99       |
|    policy_loss        | -0.0644  |
|    value_loss         | 0.00216  |
------------------------------------
------------------------------------
| rollout/              |          |
|    ep_len_mean        | 33.2     |
|    ep_rew_mean        | 0.655    |
| time/                 |          |
|    fps                | 1420     |
|    iterations         | 200      |
|    time_elapsed       | 0        |
|    total_timesteps    | 1000     |
| train/                |          |
|

#### Testing 

In [16]:
a2c_model = A2C.load("saved/a2c_b")

env.reset()

mean_reward, std_reward = evaluate_policy(a2c_model, env, deterministic=True, n_eval_episodes=20)
print(f"mean_reward:{mean_reward:.2f} +/- {std_reward:.2f}")

mean_reward:0.75 +/- 0.43


/Users/aditya/miniconda3/envs/pogema/lib/python3.9/site-packages/stable_baselines3/common/evaluation.py:67: UserWarning: Evaluation environment is not wrapped with a ``Monitor`` wrapper. This may result in reporting modified episode lengths and rewards, if other wrappers happen to modify these. Consider wrapping environment first with ``Monitor`` wrapper.
  warnings.warn(


In [17]:
# RANDOM SEED
from IPython.display import SVG, display
from pogema.animation import AnimationMonitor, AnimationConfig

env = AnimationMonitor(env)

def evaluate_success_rate(model, env, num_episodes=1000):
    success_count = 0
    step_array = []
    for i in range(num_episodes):
        print(f'---{i}---')
        obs = env.reset()

        # Check if observation is a tuple and extract the first element if true.
        if isinstance(obs, tuple):
            obs = obs[0]
        max_step = 64
        steps_taken = 0
        done = truncated = False
        while not done and max_step > 0:
            action, _ = model.predict(obs)
            next_obs, reward, done, truncated, info = env.step(action)
            print(action,max_step,success_count,done)
            max_step -= 1
            steps_taken += 1
            # Check if next_obs is a tuple and extract the first element if true.
            if isinstance(next_obs, tuple):
                next_obs = next_obs[0]
            obs = next_obs

            # Check if agent was successful in that episode.
            if done:
                success_count += 1
                step_array.append(steps_taken)
                env.save_animation(f"render{i}.svg", AnimationConfig(egocentric_idx=0))
                break

    success_rate = success_count / num_episodes
    return success_rate, step_array

success_rate,step_array = evaluate_success_rate(a2c_model, env)
print(f"Agent Success Rate: {success_rate * 100:.2f}%")
print(f"steps to termination : {step_array}")

---0---
2 64 0 False
4 63 0 False
2 62 0 False
2 61 0 False
2 60 0 False
4 59 0 False
2 58 0 True
---1---
1 64 1 True
---2---
1 64 2 False
4 63 2 False
4 62 2 False
4 61 2 False
2 60 2 False
1 59 2 False
2 58 2 False
1 57 2 False
4 56 2 False
2 55 2 False
4 54 2 False
1 53 2 False
2 52 2 False
1 51 2 False
4 50 2 False
2 49 2 False
4 48 2 False
1 47 2 False
2 46 2 False
1 45 2 False
2 44 2 False
1 43 2 False
2 42 2 False
4 41 2 False
1 40 2 False
4 39 2 False
2 38 2 False
1 37 2 False
2 36 2 False
2 35 2 False
1 34 2 False
1 33 2 False
2 32 2 False
1 31 2 False
2 30 2 False
1 29 2 False
2 28 2 False
1 27 2 False
2 26 2 False
1 25 2 False
2 24 2 False
1 23 2 False
2 22 2 False
1 21 2 False
2 20 2 False
1 19 2 False
2 18 2 False
1 17 2 False
2 16 2 False
1 15 2 False
2 14 2 False
1 13 2 False
2 12 2 False
1 11 2 False
2 10 2 False
1 9 2 False
2 8 2 False
1 7 2 False
3 6 2 False
4 5 2 False
2 4 2 False
1 3 2 False
2 2 2 False
1 1 2 False
---3---
4 64 2 False
4 63 2 False
4 62 2 True
---4-

In [18]:
step_array

[7,
 1,
 3,
 9,
 4,
 2,
 8,
 7,
 1,
 2,
 3,
 1,
 1,
 1,
 9,
 2,
 10,
 1,
 6,
 7,
 14,
 14,
 63,
 3,
 4,
 4,
 7,
 1,
 2,
 3,
 10,
 2,
 7,
 3,
 7,
 2,
 7,
 8,
 16,
 2,
 2,
 3,
 24,
 2,
 2,
 64,
 6,
 2,
 7,
 1,
 7,
 5,
 1,
 2,
 5,
 5,
 3,
 8,
 1,
 3,
 2,
 3,
 1,
 1,
 4,
 4,
 11,
 4,
 7,
 1,
 4,
 7,
 1,
 8,
 6,
 1,
 1,
 2,
 2,
 2,
 1,
 4,
 1,
 5,
 2,
 2,
 41,
 8,
 1,
 3,
 3,
 13,
 7,
 1,
 1,
 3,
 2,
 1,
 16,
 1,
 2,
 3,
 12,
 13,
 4,
 46,
 4,
 1,
 8,
 1,
 1,
 2,
 6,
 4,
 2,
 5,
 6,
 2,
 1,
 2,
 5,
 4,
 3,
 5,
 1,
 3,
 1,
 4,
 5,
 1,
 8,
 4,
 4,
 4,
 2,
 1,
 3,
 1,
 6,
 5,
 3,
 5,
 62,
 1,
 2,
 8,
 9,
 5,
 2,
 4,
 2,
 8,
 1,
 2,
 2,
 4,
 4,
 1,
 4,
 1,
 1,
 1,
 1,
 4,
 2,
 3,
 6,
 2,
 8,
 1,
 1,
 1,
 1,
 1,
 6,
 1,
 8,
 4,
 3,
 6,
 10,
 1,
 13,
 8,
 1,
 11,
 11,
 5,
 1,
 2,
 2,
 21,
 4,
 3,
 1,
 15,
 1,
 5,
 1,
 1,
 2,
 4,
 3,
 3,
 3,
 2,
 2,
 9,
 4,
 1,
 6,
 12,
 1,
 1,
 1,
 8,
 7,
 5,
 3,
 2,
 5,
 2,
 2,
 9,
 1,
 3,
 4,
 2,
 1,
 1,
 2,
 2,
 6,
 4,
 1,
 16,
 1,
 3,
 2,
 2,
 3,
 24,
 1,
 10

In [19]:
import numpy as np
np.mean(step_array)

5.222471910112359